In [1]:
import pandas as pd
import statsmodels.api as sm
import matplotlib.pyplot as plt
import seaborn as sns
import ast
import re

### Import alternate titles

In [2]:
titles_onet = pd.read_excel("Alternate Titles.xlsx")
titles_onet = titles_onet.rename(columns={'O*NET-SOC Code': 'Code'})
titles_onet['Code_prefix'] = titles_onet['Code'].str.split('-').str[0]
titles_onet

Code                                              Title   
0      11-1011.00                                   Chief Executives  \
1      11-1011.00                                   Chief Executives   
2      11-1011.00                                   Chief Executives   
3      11-1011.00                                   Chief Executives   
4      11-1011.00                                   Chief Executives   
...           ...                                                ...   
60506  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60507  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60508  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60509  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60510  55-3019.00  Military Enlisted Tactical Operations and Air/...   

                                         Alternate Title Short Title   
0                        Aeronautics Commission Director         NaN  \
1                         Agricultural Services Director         NaN   
2      Alcohol and Drug Abuse Assistance Program Admi...         NaN   
3                   Arts and Humanities Council Director         NaN   
4                                         Bakery Manager         NaN   
...                                                  ...         ...   
60506                                 Tactical Debriefer         NaN   
60507  Tactical/Mobile (Tacmobile) Ashore Analysis Sy...         NaN   
60508                         Target Aircraft Technician         NaN   
60509  Technical Surveillance Countermeasures (TSCM) ...         NaN   
60510                Unattended Ground Sensor Specialist         NaN   

      Source(s) Code_prefix  
0            08          11  
1            08          11  
2            08          11  
3            08          11  
4            08          11  
...         ...         ...  
60506        04          55  
60507        04          55  
60508        08          55  
60509        04          55  
60510        08          55  

[60511 rows x 6 columns]

In [3]:
# Rename the column
titles_onet = titles_onet.rename(columns={'O*NET-SOC Code': 'Code'})

# Extract the prefix from the 'Code' column
titles_onet['Code_prefix'] = titles_onet['Code'].str.split('-').str[0]

# Group by 'Code_prefix' and get the 9 most common alternative titles for each group
most_common_alternate_titles = titles_onet.groupby('Code_prefix')['Alternate Title'].apply(lambda x: x.value_counts().head(15)).reset_index()

most_common_alternate_titles = most_common_alternate_titles.rename(columns={'level_1': 'Alternate Title', 'Alternate Title': 'Count'})
most_common_alternate_titles.to_excel("most_common_alternate_titles.xlsx")
most_common_alternate_titles

Code_prefix                                    Alternate Title  Count
0            11                                 Operations Manager      6
1            11                                   Business Manager      5
2            11                                    Program Manager      4
3            11                                     Superintendent      4
4            11                                   Program Director      4
..          ...                                                ...    ...
340          55                    Field Artillery Senior Sergeant      2
341          55  Space And Missile Operations, Missile Combat Crew      2
342          55                               Intelligence Officer      2
343          55           Fixed-Wing Transport Aircraft Specialist      2
344          55                                     Combat Control      2

[345 rows x 3 columns]

## Import archived vacancies

In [4]:
archivedvacancies = pd.read_csv("vacancies_archivedvacancies.csv")

# Convert list-like columns to string representations
for col in archivedvacancies.columns:
    archivedvacancies[col] = archivedvacancies[col].apply(lambda x: str(x) if isinstance(x, list) else x)

# Drop duplicate enries (if any)
archivedvacancies = archivedvacancies.drop_duplicates()
archivedvacancies.reset_index(inplace=True, drop=True)

# Convert back to list
archivedvacancies['onetcodes'] = archivedvacancies['onetcodes'].apply(ast.literal_eval)

archivedvacancies

jvid   
0       009A4417625C41A28040214B89295C57206  \
1       033BBF50551A4FB1A1ECBF71992E2E1C206   
2       037A52B1C6744742B39C719ED4357F9A206   
3       04AB148C1EEE44D2A375FD0DE7286ED4206   
4       05C342151AD74749819119CE08687685206   
...                                     ...   
309585  B41DE39D9A0C413893945B30A2AD0B3D206   
309586  B249CD07798B4B268A8C349FCA88B571206   
309587  E884F325137B4C0DB9F0E04CBEFCB726206   
309588  F97403E8DA874DF8973B0DF9567E66F6206   
309589  EF31CC2F50654ACBB3CC3767D68E238E206   

                                                 jobtitle   
0       Behavior Intervention Specialist II - DDA019- ...  \
1                                  Office Coordinator III   
2                             CLINICAL PHARMACIST (STAFF)   
3                           Associate Director, Analytics   
4                                        Registered Nurse   
...                                                   ...   
309585           Senior Technical Program Manager-ProdDev   
309586                        Registered Nurse (Dialysis)   
309587  Manager, Software Engineering, Full Stack (Spa...   
309588               NY Expansion Facilities Cost Manager   
309589  Associate Director, Investment Banking - Sponsors   

                                                 company           location   
0                                       WellLife Network         Elmont, NY  \
1                                    Syracuse University       Syracuse, NY   
2       Veterans Affairs, Veterans Health Administration       New York, NY   
3                                        Publicis Groupe       New York, NY   
4                        SUNY Upstate Medical University       Syracuse, NY   
...                                                  ...                ...   
309585                                            Oracle         Albany, NY   
309586                                  Northwell Health      Manhasset, NY   
309587                         Capital One Services, LLC       New York, NY   
309588                           Micron Technology, Inc.           Clay, NY   
309589                                        Scotiabank  New York City, NY   

        dateposted                             onetcodes   
0       2024-01-25  [21-1011.00, 21-1023.00, 21-1093.00]  \
1       2024-02-22  [43-6011.00, 43-6014.00, 43-9061.00]   
2       2024-02-14                          [29-1051.00]   
3       2024-02-13  [11-9199.00, 27-2012.03, 27-3031.00]   
4       2024-01-25  [29-1141.00, 29-1141.01, 29-1141.03]   
...            ...                                   ...   
309585  2024-05-23                          [11-3021.00]   
309586  2024-05-23  [29-1141.00, 29-1141.01, 29-1141.04]   
309587  2024-05-22                          [11-3021.00]   
309588  2024-05-23  [11-1021.00, 11-3051.00, 17-2112.00]   
309589  2024-05-23  [11-3031.00, 11-9199.00, 41-3031.00]   

                                        short_description  
0       The Behavior Intervention Specialist II works ...  
1       This Office Coordinator III position provides ...  
2       The clinical pharmacist is responsible for ana...  
3       The job entails working as an Associate Direct...  
4       This job involves providing nursing care to pa...  
...                                                   ...  
309585  The Technical Program Manager (TPM) will be re...  
309586  The job entails providing age-specific patient...  
309587  The job is for a Manager, Software Engineering...  
309588  The NY Facilities Cost Manager at Micron Techn...  
309589  The Associate Director, Investment Banking - S...  

[309590 rows x 7 columns]

In [5]:
# Explode the onetcodes column
archivedvacancies_exploded = archivedvacancies.explode('onetcodes')
# Extract the 2-digit ONET code
archivedvacancies_exploded['Code_prefix'] = archivedvacancies_exploded['onetcodes'].str.split('-').str[0]
archivedvacancies_exploded

jvid   
0       009A4417625C41A28040214B89295C57206  \
0       009A4417625C41A28040214B89295C57206   
0       009A4417625C41A28040214B89295C57206   
1       033BBF50551A4FB1A1ECBF71992E2E1C206   
1       033BBF50551A4FB1A1ECBF71992E2E1C206   
...                                     ...   
309588  F97403E8DA874DF8973B0DF9567E66F6206   
309588  F97403E8DA874DF8973B0DF9567E66F6206   
309589  EF31CC2F50654ACBB3CC3767D68E238E206   
309589  EF31CC2F50654ACBB3CC3767D68E238E206   
309589  EF31CC2F50654ACBB3CC3767D68E238E206   

                                                 jobtitle   
0       Behavior Intervention Specialist II - DDA019- ...  \
0       Behavior Intervention Specialist II - DDA019- ...   
0       Behavior Intervention Specialist II - DDA019- ...   
1                                  Office Coordinator III   
1                                  Office Coordinator III   
...                                                   ...   
309588               NY Expansion Facilities Cost Manager   
309588               NY Expansion Facilities Cost Manager   
309589  Associate Director, Investment Banking - Sponsors   
309589  Associate Director, Investment Banking - Sponsors   
309589  Associate Director, Investment Banking - Sponsors   

                        company           location  dateposted   onetcodes   
0              WellLife Network         Elmont, NY  2024-01-25  21-1011.00  \
0              WellLife Network         Elmont, NY  2024-01-25  21-1023.00   
0              WellLife Network         Elmont, NY  2024-01-25  21-1093.00   
1           Syracuse University       Syracuse, NY  2024-02-22  43-6011.00   
1           Syracuse University       Syracuse, NY  2024-02-22  43-6014.00   
...                         ...                ...         ...         ...   
309588  Micron Technology, Inc.           Clay, NY  2024-05-23  11-3051.00   
309588  Micron Technology, Inc.           Clay, NY  2024-05-23  17-2112.00   
309589               Scotiabank  New York City, NY  2024-05-23  11-3031.00   
309589               Scotiabank  New York City, NY  2024-05-23  11-9199.00   
309589               Scotiabank  New York City, NY  2024-05-23  41-3031.00   

                                        short_description Code_prefix  
0       The Behavior Intervention Specialist II works ...          21  
0       The Behavior Intervention Specialist II works ...          21  
0       The Behavior Intervention Specialist II works ...          21  
1       This Office Coordinator III position provides ...          43  
1       This Office Coordinator III position provides ...          43  
...                                                   ...         ...  
309588  The NY Facilities Cost Manager at Micron Techn...          11  
309588  The NY Facilities Cost Manager at Micron Techn...          17  
309589  The Associate Director, Investment Banking - S...          11  
309589  The Associate Director, Investment Banking - S...          11  
309589  The Associate Director, Investment Banking - S...          41  

[654882 rows x 8 columns]

In [6]:
# Rename columns for consistency
titles_onet = titles_onet.rename(columns={'O*NET-SOC Code': 'Code'})
titles_onet['Code_prefix'] = titles_onet['Code'].str.split('-').str[0]

# Convert both 'Alternate Title' and 'jobtitle' columns to lowercase for comparison
titles_onet['Alternate Title Lower'] = titles_onet['Alternate Title'].str.lower()
archivedvacancies_exploded['jobtitle_lower'] = archivedvacancies_exploded['jobtitle'].str.lower()

# Escape special characters in 'Alternate Title Lower'
titles_onet['Alternate Title Lower'] = titles_onet['Alternate Title Lower'].apply(re.escape)

# Function to escape only the backslash
def escape_backslash(text):
    return text.replace('\\', '')

# Apply the custom function
titles_onet['Alternate Title Lower'] = titles_onet['Alternate Title Lower'].apply(escape_backslash)


In [7]:
archivedvacancies_exploded = archivedvacancies_exploded[~archivedvacancies_exploded['onetcodes'].str.contains("99-")]
archivedvacancies_exploded.reset_index(inplace=True)
archivedvacancies_exploded

index                                 jvid   
0            0  009A4417625C41A28040214B89295C57206  \
1            0  009A4417625C41A28040214B89295C57206   
2            0  009A4417625C41A28040214B89295C57206   
3            1  033BBF50551A4FB1A1ECBF71992E2E1C206   
4            1  033BBF50551A4FB1A1ECBF71992E2E1C206   
...        ...                                  ...   
587899  309588  F97403E8DA874DF8973B0DF9567E66F6206   
587900  309588  F97403E8DA874DF8973B0DF9567E66F6206   
587901  309589  EF31CC2F50654ACBB3CC3767D68E238E206   
587902  309589  EF31CC2F50654ACBB3CC3767D68E238E206   
587903  309589  EF31CC2F50654ACBB3CC3767D68E238E206   

                                                 jobtitle   
0       Behavior Intervention Specialist II - DDA019- ...  \
1       Behavior Intervention Specialist II - DDA019- ...   
2       Behavior Intervention Specialist II - DDA019- ...   
3                                  Office Coordinator III   
4                                  Office Coordinator III   
...                                                   ...   
587899               NY Expansion Facilities Cost Manager   
587900               NY Expansion Facilities Cost Manager   
587901  Associate Director, Investment Banking - Sponsors   
587902  Associate Director, Investment Banking - Sponsors   
587903  Associate Director, Investment Banking - Sponsors   

                        company           location  dateposted   onetcodes   
0              WellLife Network         Elmont, NY  2024-01-25  21-1011.00  \
1              WellLife Network         Elmont, NY  2024-01-25  21-1023.00   
2              WellLife Network         Elmont, NY  2024-01-25  21-1093.00   
3           Syracuse University       Syracuse, NY  2024-02-22  43-6011.00   
4           Syracuse University       Syracuse, NY  2024-02-22  43-6014.00   
...                         ...                ...         ...         ...   
587899  Micron Technology, Inc.           Clay, NY  2024-05-23  11-3051.00   
587900  Micron Technology, Inc.           Clay, NY  2024-05-23  17-2112.00   
587901               Scotiabank  New York City, NY  2024-05-23  11-3031.00   
587902               Scotiabank  New York City, NY  2024-05-23  11-9199.00   
587903               Scotiabank  New York City, NY  2024-05-23  41-3031.00   

                                        short_description Code_prefix   
0       The Behavior Intervention Specialist II works ...          21  \
1       The Behavior Intervention Specialist II works ...          21   
2       The Behavior Intervention Specialist II works ...          21   
3       This Office Coordinator III position provides ...          43   
4       This Office Coordinator III position provides ...          43   
...                                                   ...         ...   
587899  The NY Facilities Cost Manager at Micron Techn...          11   
587900  The NY Facilities Cost Manager at Micron Techn...          17   
587901  The Associate Director, Investment Banking - S...          11   
587902  The Associate Director, Investment Banking - S...          11   
587903  The Associate Director, Investment Banking - S...          41   

                                           jobtitle_lower  
0       behavior intervention specialist ii - dda019- ...  
1       behavior intervention specialist ii - dda019- ...  
2       behavior intervention specialist ii - dda019- ...  
3                                  office coordinator iii  
4                                  office coordinator iii  
...                                                   ...  
587899               ny expansion facilities cost manager  
587900               ny expansion facilities cost manager  
587901  associate director, investment banking - sponsors  
587902  associate director, investment banking - sponsors  
587903  associate director, investment banking - sponsors  

[587904 rows x 10 columns]

In [8]:
archivedvacancies_exploded[archivedvacancies_exploded["jobtitle_lower"].str.contains("software engineer")]

index                                 jvid   
900        419  C077DCE5AB13467D93C14C233246ED8D206  \
6578      3467  20820326717A43D5837EB08FA40337DD206   
7364      3847  9E1B7C3BC61B41DB9AC955E87AB75340206   
17995     9322  9F1C044FDC664D14A43AC5A5249EE811206   
23071    12013  411E1ED2BE2C4565A1C5C7800970B85B206   
...        ...                                  ...   
574845  303836  3643F3D91C8E45F5B92727BDBEDCA823206   
578368  305414  6AF90311332A48F9A4584527D70C593D206   
583764  307794  6E88AED8FFD74F0399DFB78CCBD28B23206   
584288  308031  90EC2A696F3F47D3B89EE3BE1B909173206   
587897  309587  E884F325137B4C0DB9F0E04CBEFCB726206   

                                                 jobtitle   
900     Software Engineer - Product (Technical Leaders...  \
6578    Embedded Software Engineer Summer Internship 2024   
7364    Software Engineer - Product (Technical Leaders...   
17995   Senior Manager, Software Engineering - Health ...   
23071   Avionics Simulation Software Engineer I (On-site)   
...                                                   ...   
574845                         Software Engineer- Product   
578368                         Software Engineer, Product   
583764      Associate Software Engineer- Mobile (Android)   
584288                   Director of Software Engineering   
587897  Manager, Software Engineering, Full Stack (Spa...   

                          company        location  dateposted   onetcodes   
900                          Meta    New York, NY  2024-01-25  41-9031.00  \
6578                        WATTS    Blauvelt, NY  2024-01-26  17-2072.00   
7364                         Meta    New York, NY  2024-01-26  41-9031.00   
17995                      Oracle      Albany, NY  2024-02-15  11-3021.00   
23071             RTX Corporation  Binghamton, NY  2024-02-13  17-2011.00   
...                           ...             ...         ...         ...   
574845       Meta Platforms, Inc.    New York, NY  2024-05-14  41-9031.00   
578368       Meta Platforms, Inc.    New York, NY  2024-05-14  41-9031.00   
583764                   Marriott      Albany, NY  2024-06-06  17-2112.01   
584288           American Express    New York, NY  2024-05-30  11-3021.00   
587897  Capital One Services, LLC    New York, NY  2024-05-22  11-3021.00   

                                        short_description Code_prefix   
900     Facebook is seeking experienced full-stack sof...          41  \
6578    The job entails supporting firmware developmen...          17   
7364    Facebook is seeking experienced full-stack sof...          41   
17995   This job involves leading a team in the develo...          11   
23071   Collins Aerospace is seeking an Associate Soft...          17   
...                                                   ...         ...   
574845  The Software Engineer- Product position at Met...          41   
578368  The Software Engineer, Product position at Met...          41   
583764  Join the Mobile Engineering team at Marriott I...          17   
584288  The job entails leading the development team a...          11   
587897  The job is for a Manager, Software Engineering...          11   

                                           jobtitle_lower  
900     software engineer - product (technical leaders...  
6578    embedded software engineer summer internship 2024  
7364    software engineer - product (technical leaders...  
17995   senior manager, software engineering - health ...  
23071   avionics simulation software engineer i (on-site)  
...                                                   ...  
574845                         software engineer- product  
578368                         software engineer, product  
583764      associate software engineer- mobile (android)  
584288                   director of software engineering  
587897  manager, software engineering, full stack (spa...  

[138 rows x 10 columns]

In [9]:
titles_onet

Code                                              Title   
0      11-1011.00                                   Chief Executives  \
1      11-1011.00                                   Chief Executives   
2      11-1011.00                                   Chief Executives   
3      11-1011.00                                   Chief Executives   
4      11-1011.00                                   Chief Executives   
...           ...                                                ...   
60506  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60507  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60508  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60509  55-3019.00  Military Enlisted Tactical Operations and Air/...   
60510  55-3019.00  Military Enlisted Tactical Operations and Air/...   

                                         Alternate Title Short Title   
0                        Aeronautics Commission Director         NaN  \
1                         Agricultural Services Director         NaN   
2      Alcohol and Drug Abuse Assistance Program Admi...         NaN   
3                   Arts and Humanities Council Director         NaN   
4                                         Bakery Manager         NaN   
...                                                  ...         ...   
60506                                 Tactical Debriefer         NaN   
60507  Tactical/Mobile (Tacmobile) Ashore Analysis Sy...         NaN   
60508                         Target Aircraft Technician         NaN   
60509  Technical Surveillance Countermeasures (TSCM) ...         NaN   
60510                Unattended Ground Sensor Specialist         NaN   

      Source(s) Code_prefix                              Alternate Title Lower  
0            08          11                    aeronautics commission director  
1            08          11                     agricultural services director  
2            08          11  alcohol and drug abuse assistance program admi...  
3            08          11               arts and humanities council director  
4            08          11                                     bakery manager  
...         ...         ...                                                ...  
60506        04          55                                 tactical debriefer  
60507        04          55  tactical/mobile (tacmobile) ashore analysis sy...  
60508        08          55                         target aircraft technician  
60509        04          55  technical surveillance countermeasures (tscm) ...  
60510        08          55                unattended ground sensor specialist  

[60511 rows x 7 columns]

In [17]:
# Rename columns for consistency
titles_onet = titles_onet.rename(columns={'O*NET-SOC Code': 'Code'})
titles_onet['Code_prefix'] = titles_onet['Code'].str.split('-').str[0]

# Convert both 'Alternate Title' and 'jobtitle' columns to lowercase for comparison
titles_onet['Alternate Title Lower'] = titles_onet['Alternate Title'].str.lower()
archivedvacancies_exploded['jobtitle_lower'] = archivedvacancies_exploded['jobtitle'].str.lower()

# Escape special characters in 'Alternate Title Lower'
titles_onet['Alternate Title Lower'] = titles_onet['Alternate Title Lower'].apply(re.escape)

results = []

total_titles = len(titles_onet)
titles_checked = 0

for prefix, group in titles_onet.groupby('Code_prefix'):

    # Filter job titles with the same code prefix
    jobtitles = archivedvacancies_exploded['jobtitle_lower']

    #jobtitles = archivedvacancies_exploded[archivedvacancies_exploded['Code_prefix'] == prefix]['jobtitle_lower']

    
    # Match
    for title in group['Alternate Title Lower']:
        count = jobtitles.str.contains(title).sum()
        results.append({'Code_prefix': prefix, 'Alternate Title': title, 'Count': count})
        titles_checked += 1
        print(f"Checked {titles_checked} out of {total_titles} alternate titles")

results_df = pd.DataFrame(results)

# Remove duplicates by taking only the first occurrence of each title within each Code_prefix
results_df = results_df.drop_duplicates(subset=['Code_prefix', 'Alternate Title'])

/var/folders/r0/j9sv4j853_93f6nrmgcc4bgh0000gn/T/ipykernel_95927/1052109675.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  archivedvacancies_exploded['jobtitle_lower'] = archivedvacancies_exploded['jobtitle'].str.lower()


Checked 1 out of 60511 alternate titles
Checked 2 out of 60511 alternate titles
Checked 3 out of 60511 alternate titles
Checked 4 out of 60511 alternate titles
Checked 5 out of 60511 alternate titles
Checked 6 out of 60511 alternate titles
Checked 7 out of 60511 alternate titles
Checked 8 out of 60511 alternate titles
Checked 9 out of 60511 alternate titles
Checked 10 out of 60511 alternate titles
Checked 11 out of 60511 alternate titles
Checked 12 out of 60511 alternate titles
Checked 13 out of 60511 alternate titles
Checked 14 out of 60511 alternate titles
Checked 15 out of 60511 alternate titles
Checked 16 out of 60511 alternate titles
Checked 17 out of 60511 alternate titles
Checked 18 out of 60511 alternate titles
Checked 19 out of 60511 alternate titles
Checked 20 out of 60511 alternate titles
Checked 21 out of 60511 alternate titles
Checked 22 out of 60511 alternate titles
Checked 23 out of 60511 alternate titles
Checked 24 out of 60511 alternate titles
Checked 25 out of 60511 a

In [18]:
results_df.to_excel("title_counts_across.xlsx")

In [ ]:
# Rename columns for consistency
titles_onet = titles_onet.rename(columns={'O*NET-SOC Code': 'Code'})
titles_onet['Code_prefix'] = titles_onet['Code'].str.split('-').str[0]

# Convert both 'Alternate Title' and 'jobtitle' columns to lowercase for comparison
titles_onet['Alternate Title Lower'] = titles_onet['Alternate Title'].str.lower()
archivedvacancies_exploded['jobtitle_lower'] = archivedvacancies_exploded['jobtitle'].str.lower()

# Escape special characters in 'Alternate Title Lower'
titles_onet['Alternate Title Lower'] = titles_onet['Alternate Title Lower'].apply(re.escape)

results = []

total_titles = len(titles_onet)
titles_checked = 0

for prefix, group in titles_onet.groupby('Code_prefix'):

    # Filter job titles with the same code prefix
    jobtitles = archivedvacancies_exploded['jobtitle_lower']

    jobtitles = archivedvacancies_exploded[archivedvacancies_exploded['Code_prefix'] == prefix]['jobtitle_lower']

    
    # Match
    for title in group['Alternate Title Lower']:
        count = jobtitles.str.contains(title).sum()
        results.append({'Code_prefix': prefix, 'Alternate Title': title, 'Count': count})
        titles_checked += 1
        print(f"Checked {titles_checked} out of {total_titles} alternate titles")

results_df_within = pd.DataFrame(results)

# Remove duplicates by taking only the first occurrence of each title within each Code_prefix
results_df_within = results_df_within.drop_duplicates(subset=['Code_prefix', 'Alternate Title'])

/var/folders/r0/j9sv4j853_93f6nrmgcc4bgh0000gn/T/ipykernel_95927/3120766232.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  archivedvacancies_exploded['jobtitle_lower'] = archivedvacancies_exploded['jobtitle'].str.lower()


Checked 1 out of 60511 alternate titles
Checked 2 out of 60511 alternate titles
Checked 3 out of 60511 alternate titles
Checked 4 out of 60511 alternate titles
Checked 5 out of 60511 alternate titles
Checked 6 out of 60511 alternate titles
Checked 7 out of 60511 alternate titles
Checked 8 out of 60511 alternate titles
Checked 9 out of 60511 alternate titles
Checked 10 out of 60511 alternate titles
Checked 11 out of 60511 alternate titles
Checked 12 out of 60511 alternate titles
Checked 13 out of 60511 alternate titles
Checked 14 out of 60511 alternate titles
Checked 15 out of 60511 alternate titles
Checked 16 out of 60511 alternate titles
Checked 17 out of 60511 alternate titles
Checked 18 out of 60511 alternate titles
Checked 19 out of 60511 alternate titles
Checked 20 out of 60511 alternate titles
Checked 21 out of 60511 alternate titles
Checked 22 out of 60511 alternate titles
Checked 23 out of 60511 alternate titles
Checked 24 out of 60511 alternate titles
Checked 25 out of 60511 a

In [ ]:
results_df_within.to_excel("title_counts.xlsx")

In [13]:
# Get the 9 most common alternate titles within each Code_prefix
most_common_alternate_titles = results_df.groupby('Code_prefix').apply(lambda x: x.nlargest(20, 'Count')).reset_index(drop=True)
most_common_alternate_titles['Alternate Title'] = most_common_alternate_titles['Alternate Title'].str.replace(r'\\', '', regex=True)
most_common_alternate_titles

Code_prefix                      Alternate Title  Count
0            11                              manager  42201
1            11                             director  17190
2            11                            president   3006
3            11                       vice president   2963
4            11                      program manager   2937
..          ...                                  ...    ...
455          55  catapult and arresting gear officer      0
456          55                  flight deck officer      0
457          55               landing signal officer      0
458          55        v/stol landing signal officer      0
459          55                        armor officer      0

[460 rows x 3 columns]

In [15]:
most_common_alternate_titles.to_excel("most_common_alternate_titles_in_vacancies.xlsx")